In [1]:
import os
import shutil
import contextlib
import pathlib
import json

import numpy as np
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq

import run
import environment
import evolve
import encode
import plot

from utils import ClassEncoder

In [2]:
run1_results_dir = 'results/sector-vision_sbx_simple/'

organism_vision_range = 1
run1_vision = environment.SectorVision(
    distance=organism_vision_range,
    distance_sectors=4,
    angle_sectors=6,
)
run1_genome_size = [run1_vision.organism_input_shape, 12, 2]

fitness = evolve.EnergyFitness()

arguments = {
    'start_organism_number': 40,
    'width': 20,
    'height': 20,
    'iterations': 80 * 100,
    'generation_time': 80,
    'organism_size': 0.12,
    'food_size': 0.05,
    'organism_vision_range': organism_vision_range,
    'results_dir': run1_results_dir,
    'vision': run1_vision,
    'food_energy': 2,
    'food_appearance_number_rate': 0.7,
    'encoding': encode.RealValued(),
    'selection': evolve.TruncationSelection(fitness=fitness, n=20),
    'crossover': evolve.SBXCrossover(n=2),
    'mutation': evolve.GaussianMutation(mu=0, sigma=0.1, p=0.2),
    'elitism': 5,
    'genome_size': run1_genome_size,
    'food_particles_at_start': 40,
    'remove_dead_organisms': False,
}

run1_params_file = os.path.join(run1_results_dir, 'metadata.json')

In [3]:
if os.path.exists(run1_results_dir):
    ans = input('Previous results folder exists. Do you want to delete it?')
    if ans == 'y':
        shutil.rmtree(run1_results_dir)

with contextlib.suppress(Exception):
    os.mkdir(run1_results_dir)
    
with open(run1_params_file, 'w') as file:
    json.dump(arguments, file, cls=ClassEncoder)

run1 = run.OrganismsSimpleEnvironmentRunTool(**arguments)
run1.run()

Simulating organisms: 100%|██████████| 8000/8000 [29:30<00:00,  4.52it/s, Number of organisms=25, Gen=99]


In [4]:
org_loc = pq.read_table(os.path.join(run1_results_dir,
                                     'organisms_locations')).to_pandas()
org_stat = pq.read_table(os.path.join(run1_results_dir,
                                      'organisms_stats')).to_pandas()
food_loc = pq.read_table(os.path.join(run1_results_dir,
                                      'food_locations')).to_pandas()
food_stat = pq.read_table(os.path.join(run1_results_dir,
                                       'eaten_food')).to_pandas()


org_loc.reset_index(drop=True, inplace=True)
org_stat.reset_index(drop=True, inplace=True)
food_loc.reset_index(drop=True, inplace=True)
food_stat.reset_index(drop=True, inplace=True)

In [5]:
org_loc.describe()

index              x              y          theta   
count  201200.000000  201200.000000  201200.000000  201200.000000  \
mean     1009.658052       9.461462       9.874427       2.582585   
std       580.806243       5.885350       5.832716       7.116932   
min         0.000000       0.000000       0.000000     -32.000000   
25%       508.000000       4.321865       4.825782      -0.581875   
50%      1011.000000       9.290173       9.719124       1.750049   
75%      1513.000000      14.559972      14.950675       5.701101   
max      2019.000000      20.000000      20.000000      36.795917   

           iteration     generation              v              a   
count  201200.000000  201200.000000  201200.000000  201200.000000  \
mean     3975.881710      49.204771      -0.065458      -0.037673   
std      2322.611613      29.031210       0.047411       0.031915   
min         0.000000       0.000000      -0.099999      -0.050000   
25%      1963.750000      24.000000      -0.085858      -0.050000   
50%      3975.500000      49.000000      -0.083333      -0.050000   
75%      5987.250000      74.000000      -0.083333      -0.050000   
max      7999.000000      99.000000       0.099994       0.050000   

              energy            age  
count  201200.000000  201200.000000  
mean       -3.392922      55.390656  
std         3.369361      39.639119  
min       -12.800000       0.000000  
25%        -5.280000      24.000000  
50%        -2.720000      49.000000  
75%        -0.960000      74.000000  
max         8.480000     239.000000

In [6]:
org_stat.describe()

id            age      iteration         energy
count  201200.000000  201200.000000  201200.000000  201200.000000
mean     1009.658052      55.390656    3975.881710      -3.392922
std       580.806243      39.639119    2322.611613       3.369361
min         0.000000       0.000000       0.000000     -12.800000
25%       508.000000      24.000000    1963.750000      -5.280000
50%      1011.000000      49.000000    3975.500000      -2.720000
75%      1513.000000      74.000000    5987.250000      -0.960000
max      2019.000000     239.000000    7999.000000       8.480000

In [7]:
food_stat.describe()

organism_id  food_location  energy_taken    iteration
count  4828.000000    4828.000000        4828.0  4828.000000
mean   1116.197183       9.933885           2.0  4396.463960
std     541.457340       5.751512           0.0  2165.803017
min       3.000000       0.001793           2.0     2.000000
25%     661.000000       4.865378           2.0  2574.000000
50%    1117.000000       9.827818           2.0  4402.500000
75%    1597.000000      14.911014           2.0  6318.000000
max    2019.000000      19.987308           2.0  7996.000000

In [8]:
org_loc.groupby('generation')[['energy', 'age']].describe()

energy                                                       age   
             count     mean       std    min   25%   50%   75%   max   count   
generation                                                                     
0           3200.0 -2.98125  1.934740  -6.40 -4.56 -2.96 -1.36  2.80  3200.0  \
1           2000.0 -4.44600  3.182161 -12.80 -5.92 -3.92 -1.98  0.00  2000.0   
2           2000.0 -4.29400  3.160050 -12.72 -5.92 -3.76 -1.84  1.84  2000.0   
3           2000.0 -4.03000  3.411129 -12.72 -5.84 -3.36 -1.44  3.76  2000.0   
4           2000.0 -4.16500  3.278388 -12.72 -5.84 -3.52 -1.60  1.76  2000.0   
...            ...      ...       ...    ...   ...   ...   ...   ...     ...   
95          2000.0 -3.30800  3.375552 -12.72 -5.36 -2.32 -0.80  3.92  2000.0   
96          2000.0 -2.97900  3.408543 -12.72 -4.72 -2.48 -0.88  6.32  2000.0   
97          2000.0 -3.79400  3.141353 -12.72 -5.44 -3.12 -1.36  1.52  2000.0   
98          2000.0 -3.25100  3.256019 -12.72 -5.28 -2.40 -0.80  2.88  2000.0   
99          2000.0 -3.17500  3.512017 -12.72 -5.14 -2.16 -0.64  4.40  2000.0   

                                                             
            mean        std  min    25%   50%    75%    max  
generation                                                   
0           40.5  23.095815  1.0  20.75  40.5  60.25   80.0  
1           55.7  39.797009  0.0  24.75  49.5  74.25  160.0  
2           55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
3           55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
4           55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
...          ...        ...  ...    ...   ...    ...    ...  
95          55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
96          55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
97          55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
98          55.5  39.471876  0.0  24.75  49.5  74.25  159.0  
99          55.5  39.471876  0.0  24.75  49.5  74.25  159.0  

[100 rows x 16 columns]

In [9]:
# frames_dir = os.path.join(run1_results_dir, 'frames')
# frames_dir = pathlib.Path(run1_results_dir, 'frames')
# frames_dir.mkdir()
# plot.create_frames(org_loc, food_loc, arguments['width'], arguments['height'], arguments['organism_size'], arguments['food_size'], frames_dir)

In [10]:
# plot.generate_video(
#     os.path.join(run1_results_dir, 'frames/'),
#     framerate=24,
#     output=f'{run1_results_dir}evolution.mp4',
# )

# Inspecting results

In [11]:
from plotly import express as px
import plotly.graph_objs as go

In [12]:
WINDOW = 80

moving_age_mean = org_loc[[
    'iteration', 'age'
]].groupby('iteration').mean().rolling(WINDOW).mean()

moving_age_max = org_loc[['iteration', 'age'
                          ]].groupby('iteration').max().rolling(WINDOW).mean()

moving_energy_mean = org_loc[[
    'iteration', 'energy'
]].groupby('iteration').mean().rolling(WINDOW).mean()

moving_energy_max = org_loc[[
    'iteration', 'energy'
]].groupby('iteration').max().rolling(WINDOW).mean()

x = np.arange(len(moving_age_max))

ma_age = go.Scatter(
    x=x,
    y=moving_age_mean['age'],
    name=f'Moving Age Average {WINDOW}',
    mode='lines',
    legendgroup='Age',
)
mm_age = go.Scatter(x=x,
                    y=moving_age_max['age'],
                    name=f'Moving Age Max {WINDOW}',
                    mode='lines',
                    legendgroup='Age')
ma_energy = go.Scatter(x=x,
                       y=moving_energy_mean['energy'],
                       name=f'Moving Energy Average {WINDOW}',
                       mode='lines',
                       legendgroup='Energy')
mm_energy = go.Scatter(x=x,
                       y=moving_energy_max['energy'],
                       name=f'Moving Energy Max {WINDOW}',
                       mode='lines',
                       legendgroup='Energy')

layout = go.Layout(title='Evolution Statistics',
                   xaxis=dict(title='Time'))

fig = go.Figure(data=[mm_energy, ma_energy], layout=layout)
# fig = go.Figure(data=[ma_age, mm_age, mm_energy, ma_energy], layout=layout)
fig.show()

In [13]:
WINDOW = 3

moving_age_mean = org_loc[[
    'generation', 'age'
]].groupby('generation').mean().rolling(WINDOW).mean()

moving_age_max = org_loc[['generation', 'age'
                          ]].groupby('generation').max().rolling(WINDOW).mean()

moving_energy_mean = org_loc[['generation', 'energy']].groupby('generation').mean().rolling(WINDOW).mean()

moving_energy_max = org_loc[['generation', 'energy']].groupby('generation').max().rolling(WINDOW).mean()

x = np.arange(len(moving_age_max))

ma_age = go.Scatter(
    x=x,
    y=moving_age_mean['age'],
    name=f'Moving Age Average {WINDOW}',
    mode='lines',
    legendgroup='Age',
)

mm_age = go.Scatter(x=x,
                    y=moving_age_max['age'],
                    name=f'Moving Age Max {WINDOW=}',
                    mode='lines',
                    legendgroup='Age')

ma_energy = go.Scatter(x=x,
                    y=moving_energy_mean['energy'],
                    name=f'Moving Energy Max {WINDOW=}',
                    mode='lines',
                    legendgroup='Energy')

mm_energy = go.Scatter(x=x,
                    y=moving_energy_mean['energy'],
                    name=f'Moving Energy Average {WINDOW=}',
                    mode='lines',
                    legendgroup='Energy')

layout = go.Layout(title='Evolution Statistics',
                   xaxis=dict(title='Generation'))

fig = go.Figure(data=[ma_age, mm_age, mm_energy, ma_energy], layout=layout)
fig.show()

In [14]:
age_mean = org_loc[[
    'generation', 'age'
]].groupby('generation').mean()

age_max = org_loc[['generation', 'age'
                          ]].groupby('generation').max()

energy_mean = org_loc[['generation', 'energy']].groupby('generation').mean()

energy_max = org_loc[['generation', 'energy']].groupby('generation').max()

energy_max_ma = energy_max.rolling(5).mean()

x = np.arange(len(age_max))

age_avg = go.Scatter(
    x=x,
    y=age_mean['age'],
    name=f'Age Average',
    mode='lines',
    legendgroup='Age',
)

age_max = go.Scatter(x=x,
                    y=age_max['age'],
                    name=f'Age Max',
                    mode='lines',
                    legendgroup='Age')

energy_mean = go.Scatter(x=x,
                    y=energy_mean['energy'],
                    name=f'Energy Average',
                    mode='lines',
                    legendgroup='Energy')

energy_max = go.Scatter(x=x,
                    y=energy_max['energy'],
                    name=f'Energy Max',
                    mode='lines',
                    marker_color='rgba(255, 180, 0, 100)',
                    legendgroup='Energy')

energy_max_ma = go.Scatter(x=x,
                    y=energy_max_ma['energy'],
                    name=f'MA Energy Max',
                    mode='lines',
                    marker_color='rgba(255, 50, 0, 100)',
                    legendgroup='Energy')

layout = go.Layout(title='Evolution Energy Statistics',
                   xaxis=dict(title='Generation'))

fig = go.Figure(data=[energy_mean, energy_max, energy_max_ma], layout=layout)
# fig = go.Figure(data=[age_avg, age_max, energy_mean], layout=layout)

fig.show()

In [15]:
org_loc

index          x          y      theta  name  iteration  generation   
0        1906  13.690506  18.616624  16.200000    Fe       7601          95  \
1        1910   8.985440   6.026441  -3.133847    Ja       7601          95   
2        1911  15.433100   7.783847   3.846663  Teya       7601          95   
3        1913   1.759809   9.136805   8.987206  Keti       7601          95   
4        1915   8.608594  11.379100   2.454809   Lal       7601          95   
...       ...        ...        ...        ...   ...        ...         ...   
201195    635   4.478362   6.061774   0.000000  Zupi       2400          30   
201196    636   1.091592   8.428705   0.000000  Dama       2400          30   
201197    637   0.569583   5.773399   0.000000    Na       2400          30   
201198    638   3.297511  19.662612   0.000000   Cox       2400          30   
201199    639  15.887561   6.376148   0.000000  Male       2400          30   

               v     a  energy  age  
0      -0.083333 -0.05   -6.48   81  
1      -0.083333 -0.05   -6.48   81  
2      -0.083333 -0.05   -6.48   81  
3      -0.096314 -0.05   -6.48   81  
4      -0.091048 -0.05   -6.48   81  
...          ...   ...     ...  ...  
201195  0.000000  0.00    0.00    0  
201196  0.000000  0.00    0.00    0  
201197  0.000000  0.00    0.00    0  
201198  0.000000  0.00    0.00    0  
201199  0.000000  0.00    0.00    0  

[201200 rows x 11 columns]

In [18]:
gen = 1

y = org_loc[org_loc.generation == gen]
best_index = y[y.energy == y.energy.max()].iloc[0].loc['index']
best = y[y['index'] == best_index]
best = best.sort_values(by='iteration')
worst_index = y[y.energy == y.energy.min()].iloc[0]['index']
worst = y[y['index'] == worst_index]
worst = worst.sort_values(by='iteration')

worst

index         x         y  theta name  iteration  generation   
93160       1  6.391436  1.370663  -16.2    G         80           1  \
93185       1  6.455598  1.317487  -16.4    G         81           1   
93210       1  6.507917  1.252625  -16.6    G         82           1   
93235       1  6.546307  1.178661  -16.8    G         83           1   
93260       1  6.569237  1.098544  -17.0    G         84           1   
...       ...       ...       ...    ...  ...        ...         ...   
195050      1  6.206801  0.609773  -31.2    G        155           1   
195075      1  6.123478  0.608446  -31.4    G        156           1   
195100      1  6.041553  0.623699  -31.6    G        157           1   
195125      1  5.964291  0.654924  -31.8    G        158           1   
195150      1  5.894772  0.700876  -32.0    G        159           1   

               v     a  energy  age  
93160  -0.083333 -0.05   -6.48   81  
93185  -0.083333 -0.05   -6.56   82  
93210  -0.083333 -0.05   -6.64   83  
93235  -0.083333 -0.05   -6.72   84  
93260  -0.083333 -0.05   -6.80   85  
...          ...   ...     ...  ...  
195050 -0.083333 -0.05  -12.48  156  
195075 -0.083333 -0.05  -12.56  157  
195100 -0.083333 -0.05  -12.64  158  
195125 -0.083333 -0.05  -12.72  159  
195150 -0.083333 -0.05  -12.80  160  

[80 rows x 11 columns]

In [16]:
# age_mean = org_loc[[
#     'generation', 'age'
# ]].groupby('generation').mean()
# age_max = org_loc[['generation', 'age'
#                           ]].groupby('generation').max()
# energy_mean = org_loc[['generation', 'energy']].groupby('generation').mean()

x = np.arange(org_loc['iteration'].max())
gens = org_loc['generation']

fig = go.Figure()

for gen in gens[:20]:
  y = org_loc[org_loc.generation == gen]
  best_index = y[y.energy == y.energy.max()].iloc[0].loc['index']
  best = y[y['index'] == best_index]
  best = best.sort_values(by='iteration')
  worst_index = y[y.energy == y.energy.min()].iloc[0]['index']
  worst = y[y['index'] == worst_index]
  worst = worst.sort_values(by='iteration')
  # y = org_stat[org_loc['id'] == id].sort_values(by='iteration')
  fig.add_trace(go.Scatter(x=x, y=best['energy']))
  fig.add_trace(go.Scatter(x=x, y=worst['energy']))

# age_avg = go.Scatter(
#     x=x,
#     y=age_mean['age'],
#     name=f'Age Average',
#     mode='lines',
#     legendgroup='Age',
# )

# age_max = go.Scatter(x=x,
#                     y=age_max['age'],
#                     name=f'Age Max',
#                     mode='lines',
#                     legendgroup='Age')

# energy_mean = go.Scatter(x=x,
#                     y=energy_mean['energy'],
#                     name=f'Energy Average',
#                     mode='lines',
#                     legendgroup='Energy')

# layout = go.Layout(title='Evolution Statistics',
#                    xaxis=dict(title='Generation'))

# fig = go.Figure(data=[energy_mean], layout=layout)
# fig = go.Figure(data=[age_avg, age_max, energy_mean], layout=layout)

fig.show()